Let's take a look at a simple way to trying to identify some structure in our data. Getting some understanding of the data is an important first step before we even start to look at using machine learning techniques to train a model; in this notebook, we'll approach that problem from a couple of different angles.

We'll start by loading our training data.

In [1]:
!pip install --upgrade pip

In [15]:
!pip install -r requirements.txt

In [16]:
import pandas as pd
import os.path

data = pd.read_parquet(os.path.join("data", "training.parquet"))

Our training data (which we generated in [the previous notebook](00-generator.ipynb)) consists of labels (either `legitimate` or `spam`) and short documents of plausible English text.  We can inspect these data:

In [17]:
data.sample(50)

index       label                                               text
13548  13548  legitimate  I asked you as soon as we had always a turn fo...
38044  18044        spam  For some reason both my boys loved it! It tame...
22039   2039        spam  Even my son who has peanut allergies, but it i...
38745  18745        spam  I love the taste. I've tried tons of GF pancak...
38630  18630        spam  I'm sure I'll be that lucky to get an Amazon s...
22649   2649        spam  He says it's not hard to find. I will order fr...
39444  19444        spam  This variety is nice a crunchy, perfect for mi...
20377    377        spam  I have had to wait for them to process these i...
28749   8749        spam  They impart a strong chemical taste. One of th...
29696   9696        spam  I love Klein's dried cherries. It makes a perf...
29085   9085        spam  I'm a believer. Expecting good taste since it ...
7585    7585  legitimate  He is so very handsome an apology from her on ...
4225    4225  legitimate  The general attended her himself to the distre...
30750  10750        spam  I use this Sauce with so many of the chicken/d...
8407    8407  legitimate  Elizabeth felt that she would not be secure. T...
9135    9135  legitimate  You must contrive to send somebody. Equally fo...
7324    7324  legitimate  I do not think Isabella has any heart to lose....
11268  11268  legitimate  She was heartily ashamed of their own future l...
14423  14423  legitimate  She joined Charles and Mary, and was tired eno...
34236  14236        spam  BUT for my teething baby starting at 6 or 7 pe...
33219  13219        spam  That is annoying, but easily fixed by insertin...
37301  17301        spam  PLEASE DON'T BUY...IT'S NOT EVEN GOOD! I am on...
11272  11272  legitimate  Their love of society, and their new dining-ro...
3781    3781  legitimate  Supported by the conviction of very much surpa...
30145  10145        spam  There are instructions in the manual that tell...
15353  15353  legitimate  She wished to prove to him that anybody could ...
17164  17164  legitimate  It has really helped me recover faster. There ...
12932  12932  legitimate  The same warmth of sentiment which might have ...
27967   7967        spam  I've yet to find another quality food that the...
18538  18538  legitimate  When Anderson first introduced me to this bran...
35991  15991        spam  If you are someone who likes light to medium r...
3243    3243  legitimate  Scenes had passed in conversation between Wick...
406      406  legitimate  I would have everything done in the church? Th...
19478  19478  legitimate  Sir Walter has resented it. The child was to b...
17858  17858  legitimate  They were soon joined by Mrs. Collins, but lik...
21383   1383        spam  I broke them up with sugar and honey. I no lon...
24590   4590        spam  I am also concerned because these comments hav...
32011  12011        spam  I absolutely love fodarific. I recommend going...
7444    7444  legitimate  Whatever the reason, I WON'T be buying THIS co...
23311   3311        spam  I just got home and they were really warm.Even...
32859  12859        spam  I like mine better, plus...it costs less! Love...
32613  12613        spam  I'll never buy anything I haven't tried, and n...
24946   4946        spam  But the good price on Amazon. This is a delici...
4660    4660  legitimate  I feel it more, why should it wound me deeper ...
33925  13925        spam  Cherry coridals have a liquid filling; these d...
21913   1913        spam  The soil was all over the carpet. As a cold ce...
14985  14985  legitimate  The sight of Miss Price dripping with wet in t...
5127    5127  legitimate  Mrs. Weston, did you ever hear any thing so st...
25758   5758        spam  The flavor really clings to the liner making i...
15143  15143  legitimate  She was heartily ashamed of their own abominab...

Ultimately, machine learning algorithms operate on data that is structured differently than the data we might deal with in database tables or application programs.  In order to identify and exploit structure in these data, we are going to convert our natural-language documents to points in space by converting them to vectors of floating-point numbers.

This process is often tricky, since you want a way to map from arbitrary data to some points in (some) space that preserves the structure of the data.  That is, documents that are similar should map to points that are similar (for some definition of similarity), and documents that are dissimilar should not map to similar points.  The name for this process of turning real-world data into a form that a machine learning algorithm can take advantage of is *feature engineering*.  

You'll learn more about feature engineering in the next notebook; for now, we'll just take a very basic approach that will let us visualize our data.  We'll first convert our documents to *k-shingles*, or sequences of *k* characters (for some small value of *k*).  This means that a document like

`the quick brown fox jumps over the lazy dog`

would become this sequence of 4-shingles: 

`['the ', 'he q', 'e qu', ' qui', 'quic', 'uick', 'ick ', 'ck b', 'k br', ' bro', 'brow', 'rown', 'own ', 'wn f', 'n fo', ' fox', 'fox ', 'ox j', 'x ju', ' jum', 'jump', 'umps', 'mps ', 'ps o', 's ov', ' ove', 'over', 'ver ', 'er t', 'r th', ' the', 'the ', 'he l', 'e la', ' laz', 'lazy', 'azy ', 'zy d', 'y do', ' dog']`

Shingling gets us a step closer to having vector representations of documents -- ultimately, our assumption is that spam documents will have some k-shingles that legitimate documents don't, and vice versa.  Here's how we'd add a field of shingles to our data:

In [18]:
def doc2shingles(k):
    def kshingles(doc):
        return [doc[i:i + k] for i in range(len(doc) - k + 1)]
    return kshingles

data["shingles"] = data["text"].apply(doc2shingles(4))

Remember, our goal is to be able to learn a function that can separate between documents that are likely to represent legitimate messages (i.e., prose in the style of Jane Austen) or spam messages (i.e., prose in the style of food-product reviews), so we'll still want to transform our lists of shingles into vectors.

1.  We'll collect shingle counts for each example, showing us how frequent each shingle is in a given document;
2.  We'll then turn those raw counts into frequencies (i.e., for a given shingle what percentage of shingle in given document are that word?), giving us a mapping from shingles to frequencies for each document;
3.  Finally, we'll encode these mappings as fixed-size vectors in a space-efficient way, by using a hash function to determine which vector element should get a given frequency.  Hashing has a few advantages, but for our purposes the most important advantage is that we don't need to know all of the shingles we might see in advance. 

(That's what we'll _logically_ do -- we'll _actually_ do these steps a bit out of order because it will make our code simpler and more efficient without changing the results.)

In [19]:
import numpy as np

def hashing_frequency(vecsize, h):
    """ 
    returns a function that will collect shingle frequencies 
    into a vector with _vecsize_ elements and will use 
    the hash function _h_ to choose which vector element 
    to update for a given term
    """
    
    def hf(words):
        if type(words) is type(""):
            # handle both lists of words and space-delimited strings
            words = words.split(" ")
            
        result = np.zeros(vecsize)
        for term in words:
            result[h(term) % vecsize] += 1.0
        
        total = sum(result)
        for i in range(len(result)):
            result[i] /= total

        return result
        
    return hf

In [20]:
a = np.array([hashing_frequency(128, hash)(v) for v in data["shingles"].values])

So now instead of having documents (which we had from the raw data) or lists of shingles, we have vectors representing shingle frequencies.  Because we've hashed shingles into these vectors, we can't in general reconstruct a document or the shingles from a vector, but we *do* know that if the same shingle appears in two documents, their vectors will reflect it in corresponding buckets.

However, we've generated a 128-element vector.  Recall that our ultimate goal is to place documents in space so that we can identify a way to separate legitimate documents from spam documents.  Our 128-element vector is a point in a space, but it's a point in a space that most of our geometric intuitions don't apply to (some of us have enough trouble navigating the three dimensions of the physical world).  

Let's use a very basic technique to project these vectors to a much smaller space that we can visualize.  [Principal component analysis](https://en.wikipedia.org/wiki/Principal_component_analysis), or PCA, is a statistical technique that is over a century old; it takes observations in a high-dimensional space (like our 1024-element vectors) and maps them to a (potentially much) smaller number of dimensions.  It's an elegant technique, and the most important things to know about it are that it tries to ensure that the dimensions that have the most variance contribute the most to the mapping, while the dimensions with the least variance are (more-or-less) disregarded.  The other important thing to know about PCA is that there are very efficient ways to compute it, even on large datasets that don't fit in memory on a single machine.  We'll see it in action now, using the [implementation from scikit-learn](https://scikit-learn.org/stable/modules/generated/sklearn.decomposition.PCA.html#sklearn.decomposition.PCA).

In [21]:
import sklearn.decomposition

DIMENSIONS = 2

pca2 = sklearn.decomposition.PCA(DIMENSIONS)

pca_a = pca2.fit_transform(a)

The `.fit_transform()` method takes an array of high-dimensional observations and will both perform the principal component analysis (the "fit" part) and use that to map the high-dimensional values to low-dimensional ones (the "transform" part).  We can see what the transformed vectors look like:

In [22]:
pca_df = pd.DataFrame(pca_a, columns=["x", "y"])
pca_df.sample(50)

x         y
10762  0.004742 -0.004019
39517  0.012793  0.010083
4887   0.008585  0.000073
6058   0.015913 -0.008019
18715 -0.004782  0.000437
5995   0.014474 -0.001577
22142  0.018756  0.008709
2788   0.007766 -0.004590
33141  0.001990  0.011220
33026  0.002577  0.002975
24342  0.008495  0.010407
19675  0.008008 -0.008643
6893   0.003839 -0.001775
2125  -0.001891 -0.006113
4446   0.008420 -0.009652
23361  0.004624  0.016811
17670 -0.002906  0.002024
15893 -0.008684 -0.002721
36233 -0.013614  0.012305
36777 -0.013709  0.001016
18346  0.004777  0.002141
26915 -0.010355  0.013587
27431  0.008026 -0.002649
34949 -0.003066  0.001356
33417 -0.003704  0.002447
31243 -0.004170  0.008106
15460  0.010145  0.003951
39839  0.006493 -0.005673
21997  0.007251  0.008604
15869  0.009706 -0.009526
18895  0.007175 -0.004332
23160 -0.011921  0.002554
26632 -0.005636  0.002225
21559  0.002552  0.008369
1375   0.000036 -0.005143
28365  0.001630  0.005903
5758   0.003491 -0.009446
30811  0.000474  0.009342
37352  0.000662  0.009243
20533 -0.002047 -0.003166
14421 -0.008680 -0.006668
2855   0.004113 -0.004072
20520  0.006239  0.010565
36754 -0.000963 -0.003823
20059  0.009603  0.015343
5890   0.006357 -0.011077
5381  -0.000062 -0.010575
13495 -0.003265 -0.002613
8704   0.010601 -0.008269
18751 -0.001048 -0.006508

Let's plot these points to see if it looks like there is some structure in our data.  We'll use the [Altair](https://altair-viz.github.io) library, which is a declarative visualization library, meaning that the presentation of our data will depend on the data itself -- for example, we'll say to use the two elements of the vectors for *x* and *y* coordinates but to use whether a document is legitimate or spam to determine how to color the point.

We'll start by using the [`concat` function in the Pandas library](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.concat.html) to make a data frame consisting of the original data frame with the PCA vector for each row.

In [23]:
plot_data = pd.concat([data.reset_index(), pca_df], axis=1)

Our next step will be to set up Altair, tell it how to encode our data frame in a plot, by using the `.encode(...)` method to tell it which values to use for x and y coordinates, as well as which value to use to decide how to color points.  Altair will restrict us to plotting 5,000 points (so that the generated chart will not overwhelm our browser), so we'll also make sure to sample a subset of the data (in this case, 1,000 points).

In [25]:
import altair as alt
#alt.data_transformers.disable_max_rows()
alt.Chart(plot_data.sample(1000)).encode(x="x", y="y", color="label").mark_point().interactive()

alt.Chart(...)

That plot in particular is interactive (note the call to `.interactive()` at the end of the command), which means that you can pan around by dragging with the mouse or zoom with the mouse wheel.  Try it out!

Notice that, for the most part, even our simple shingling approach has identified some structure in the data: there is a clear dividing line between legitimate and spam documents.  (It's important to remember that we're only using the labels to color points after we've placed them -- the PCA transformation isn't taking labels into account when mapping the vectors to two dimensions.)

The next approach we'll try is called t-distributed stochastic neighbor embedding, or t-SNE for short.  t-SNE learns a mapping from high-dimensional points to low-dimensional points so that points that are similar in high-dimensional space are likely to be similar in low-dimensional space as well.  t-SNE can sometimes identify structure that simpler techniques like PCA can't, but this power comes at a cost:  it is much more expensive to compute than PCA and doesn't parallelize well.  (t-SNE also works best for visualizing two-dimensional data when it is reducing from tens of dimensions rather than hundreds or thousands.  So, in some cases, you'll want to use a fast technique like PCA to reduce your data to a few dozen dimensions before using t-SNE.  We haven't done that in this notebook, though.)

So we can finish this notebook quickly and get on to the rest of our material, we'll only use t-SNE to visualize a subset of our data.  We've [declared a helper function called `sample_corresponding`](mlworkflows/util.py), which takes a sequence of arrays or data frames, generates a set of random indices, and returns collections with the elements corresponding to the selected indices from each array or data frame.  So if we had the collections `[1, 2, 3, 4, 5]` and `[2, 4, 6, 8, 10]`, a call to `sample_corresponding` asking for two elements might return `[[1, 4], [2, 8]]`.

In [26]:
import sklearn.manifold
from mlworkflows import util as mlwutil

np.random.seed(0xc0ffee)
sdf, sa = mlwutil.sample_corresponding(800, data, a)

tsne = sklearn.manifold.TSNE()
tsne_a = tsne.fit_transform(sa)

In [27]:
tsne_plot_data = pd.concat([sdf.reset_index(), pd.DataFrame(tsne_a, columns=["x", "y"])], axis=1)

The Altair library, which we introduced while looking at our PCA results, is easy to use.  However, to avoid cluttering our notebooks in a common case, we've [introduced a helper function called `plot_points`](mlworkflows/plot.py) that will just take a data frame and a data encoding before generating an interactive Altair scatterplot.  (For more complicated cases, we'll still want to use Altair directly.)

In [28]:
from mlworkflows import plot

plot.plot_points(tsne_plot_data, x="x", y="y", color="label")

alt.Chart(...)

In this notebook, you've learned about two ways to visualize multidimensional data in two dimensions, which helps you to evaluate whether or not a given feature engineering approach is revealing structure in your data.  In [our next notebook](02-evaluating-models.ipynb), you'll learn how to evaluate models based on the predictions that they make.